In [ ]:
pip install git+https://github.com/noc-lab/simple_sentence_segment.git

We highly recommend our [sentence segment tool](https://github.com/noc-lab/simple_sentence_segment) for detecting sentence boundary if the text contains arbitrary line breaks, such as the sample text in the following. To use this package, just run
```
pip install git+https://github.com/noc-lab/simple_sentence_segment.git
```
Alternatively, you can use the sentence segmentation tool in NLTK or Spacy. Also, you can use other tokenization tools than NLTK. But this example uses NTLK for the illustrative purpose.

## 1. simple_sentence_segment & Library Install

In [11]:
def parse_text(text):
    # Perform sentence segmentation, tokenization and return the lists of tokens,
    # spans, and text for every sentence respectively
    tokenizer = nltk.tokenize.TreebankWordTokenizer()
    all_sentences = []
    all_spans = []
    start = 0
    normalized_text = ''
    for span in sentence_segment(text):
        sentence = text[span[0]:span[1]]
        sentence = re.sub('\n', ' ', sentence)
        sentence = re.sub(r'\ +', ' ', sentence)
        sentence = sentence.strip()

        if len(sentence) > 0:
            tokens_span = tokenizer.span_tokenize(sentence)
            tokens = []
            spans = []
            for span in tokens_span:
                tokens.append(sentence[span[0]:span[1]])
                spans.append([start + span[0], start + span[1]])
                
            all_sentences.append(tokens)
            all_spans.append(spans)
            
            start += len(sentence) + 1
            normalized_text += sentence + '\n'
    return all_sentences, all_spans, normalized_text.strip()

In [12]:
def build_display_elements(tokens, annotations, spans):
    # convert the annotations to the format used in displacy
    all_ann = []

    for sent_id, sent_info in enumerate(tokens):
        sent_length = len(tokens[sent_id])

        last_ann = 'O'
        last_start = None
        last_end = None
        for token_id in range(sent_length):
            this_ann = annotations[sent_id][token_id]

            # separated cases:
            if this_ann != last_ann:
                if last_ann != 'O':
                    # write last item
                    new_ent = {}
                    new_ent['start'] = last_start
                    new_ent['end'] = last_end
                    new_ent['label'] = last_ann[2:]
                    all_ann.append(new_ent)

                # record this instance
                last_ann = 'O' if this_ann == 'O' else 'I' + this_ann[1:]
                last_start = spans[sent_id][token_id][0]
                last_end = spans[sent_id][token_id][1]

            else:
                last_ann = this_ann
                last_end = spans[sent_id][token_id][1]

        if last_ann != 'O':
            new_ent = {}
            new_ent['start'] = last_start
            new_ent['end'] = last_end
            new_ent['label'] = last_ann[2:]
            all_ann.append(new_ent)

    return all_ann

In [27]:
import nltk
import re
import os

from spacy import displacy
from IPython.core.display import display, HTML
from simple_sentence_segment import sentence_segment

from elasticsearch import Elasticsearch
import xml.etree.ElementTree as ET
from tqdm import tqdm
import pandas as pd

In [14]:
#CCE_ASSETS = '/home2/dalya/clinical_concept_extraction/clinical_concept_extraction/cce_assets'
os.chdir('/home2/dalya/clinical_concept_extraction/')

from clinical_concept_extraction import clinical_concept_extraction
os.chdir('/home2/dalya/clinical_concept_extraction/ukyoung')

### 2. Documents-100 Load

In [31]:
### 2-1. TEST Docs
path = "/home2/ukyoung/my-python/trec-2022/12.02/output_2/"
docs = [f for f in os.listdir(path) if not f.startswith('.')] 

In [32]:
docs

['NCT00811187.txt',
 'NCT00813215.txt',
 'NCT00818467.txt',
 'NCT00815750.txt',
 'NCT00819078.txt',
 'NCT00813410.txt',
 'NCT00812682.txt',
 'NCT00811889.txt',
 'NCT00818038.txt',
 'NCT00817713.txt',
 'NCT00812630.txt',
 'NCT00815139.txt',
 'NCT00814268.txt',
 'NCT00814762.txt',
 'NCT00811096.txt',
 'NCT00816387.txt',
 'NCT00818181.txt',
 'NCT00814372.txt',
 'NCT00816751.txt',
 'NCT00816153.txt',
 'NCT00815152.txt',
 'NCT00814359.txt',
 'NCT00816465.txt',
 'NCT00811954.txt',
 'NCT00811681.txt',
 'NCT00819793.txt',
 'NCT00811460.txt',
 'NCT00815386.txt',
 'NCT00810563.txt',
 'NCT00818493.txt',
 'NCT00817492.txt',
 'NCT00814853.txt',
 'NCT00811707.txt',
 'NCT00817011.txt',
 'NCT00818233.txt',
 'NCT00813748.txt',
 'NCT00819273.txt',
 'NCT00814619.txt',
 'NCT00812565.txt',
 'NCT00814307.txt',
 'NCT00817063.txt',
 'NCT00817843.txt',
 'NCT00812097.txt',
 'NCT00814827.txt',
 'NCT00814151.txt',
 'NCT00818090.txt',
 'NCT00816933.txt',
 'NCT00814593.txt',
 'NCT00814944.txt',
 'NCT00810810.txt',


### 3. ClinicalBert Term 추출 

In [42]:
import warnings
warnings.filterwarnings('ignore')

In [ ]:
# Text -> Term Lists
def get_clinicalTerms(text: str):

    tokenized_sentences, all_spans, normalized_text = parse_text(text)
    all_annotations = clinical_concept_extraction(tokenized_sentences)
    ent = build_display_elements(tokenized_sentences, all_annotations, all_spans)

    problems, tests, treatments = [], [], []

    for e in ent:
        text = normalized_text[e['start']:e['end']]
        if e['label'] == 'problem':
            problems.append(text)
        elif e['label'] == 'test':
            tests.append(text)
        elif e['label'] == 'treatment':
            treatments.append(text)
            
    len_problems, len_tests, len_treatments = len(problems), len(tests), len(treatments)
    problems = '_'.join(filter(lambda x: x if x is not None else '', problems))
    tests = '_'.join(filter(lambda x: x if x is not None else '', tests))
    treatments = '_'.join(filter(lambda x: x if x is not None else '', treatments))
    
    return [len_problems, problems, len_tests, tests, len_treatments, treatments]

In [ ]:
import pandas as pd
def df_init():
    df = pd.DataFrame({'ncd_id': [], 
                             'title_len_problems': [], 'title_problems': [], 'title_len_tests': [], 'title_tests': [], 'title_len_treatments': [], 'title_treatments': [],
                             'summary_len_problems': [], 'summary_problems': [], 'summary_len_tests': [], 'summary_tests': [], 'summary_len_treatments': [], 'summary_treatments': [],
                             #'desc_len_problems': [''], 'desc_problems': [''], 'desc_len_tests': [''], 'desc_tests':[''], 'desc_len_treatments': [''], 'desc_treatments': [''],
                             #'condition_len_problems': [''], 'condition_problems': [''], 'condition_len_tests': [''], 'condition_tests': [''], 'condition_len_treatments': [''], 'condition_treatments': [''],
                             'incriteria_len_problems': [], 'incriteria_problems': [], 'incriteria_len_tests': [], 'incriteria_tests': [], 'incriteria_len_treatments': [], 'incriteria_treatments': [],
                             'excriteria_len_problems': [], 'excriteria_problems': [], 'excriteria_len_tests': [], 'excriteria_tests': [], 'excriteria_len_treatments': [], 'excriteria_treatments': []},
                        )
    return df
df_output = df_init()

In [ ]:
#import tensorflow as tf
#tf.compat.v1.logging.set_verbosity(tf.compat.v1.logging.Error)

#from nltk.tokenize import word_tokenize
import xml.etree.ElementTree as ET 
f_path = "/home2/dalya/TREC/CTs-processed-v1"
#f_path = "/home2/ukyoung/my-python/TREC/문서전처리_0712/CTs-processed-v1/"

current_docs = []
csv_cnt = 2
# range: 50까진 어캐 됨
for idx in range(50, len_total + 1):
    
    if idx % 100 == 0:
        df_output.to_csv(f'docs/clinicalTerms_docs_{current_docs}.csv', header=True, index=False)
        current_docs += 1
        df_output = df_init()
    
    #print(f"------IDX: {idx} Started.. ------")
    doc_path = f_path + f_list[idx][1:-1]
    with open(doc_path, 'r', encoding='UTF8') as i_f:
        doc = ET.parse(i_f)
        doc = doc.getroot()
        
        # Document ID
        ncd_id = str(doc.find('nct_id').text)
        
        # Titles
        title = str(doc.find('brief_title').text)
        title_len_problems, title_problems, title_len_tests, title_tests, title_len_treatments, title_treatments = get_clinicalTerms(title)
        
        # Summaries
        summary = str(doc.find('brief_summary').text)
        summary_len_problems, summary_problems, summary_len_tests, summary_tests, summary_len_treatments, summary_treatments = get_clinicalTerms(summary)
        
        # Descriptions
        #description = ""#str(doc.find('detailed_description').text)
        #desc_len_problems, desc_problems, desc_len_tests, desc_tests, desc_len_treatments, desc_treatments = get_clinicalTerms(description)
        
        # Conditions
        #condition = str(doc.find('condition').text)
        #condition_len_problems, condition_problems, condition_len_tests, condition_tests, condition_len_treatments, condition_treatments = get_clinicalTerms(condition)
        
        in_criteria = str(doc.find('inclusion_criteria').text)
        incriteria_len_problems, incriteria_problems, incriteria_len_tests, incriteria_tests, incriteria_len_treatments, incriteria_treatments = get_clinicalTerms(in_criteria)
        
        ex_criteria = str(doc.find('exclusion_criteria').text)
        excriteria_len_problems, excriteria_problems, excriteria_len_tests, excriteria_tests, excriteria_len_treatments, excriteria_treatments = get_clinicalTerms(ex_criteria)
        
        df_output.loc[len(df_output)] = [ncd_id, 
                             title_len_problems, title_problems, title_len_tests, title_tests, title_len_treatments, title_treatments,
                             summary_len_problems, summary_problems, summary_len_tests, summary_tests, summary_len_treatments, summary_treatments,
                             #desc_len_problems, desc_problems, desc_len_tests, desc_tests, desc_len_treatments, desc_treatments,
                             #condition_len_problems, condition_problems, condition_len_tests, condition_tests, condition_len_treatments, condition_treatments,
                             incriteria_len_problems, incriteria_problems, incriteria_len_tests, incriteria_tests, incriteria_len_treatments, incriteria_treatments,
                             excriteria_len_problems, excriteria_problems, excriteria_len_tests, excriteria_tests, excriteria_len_treatments, excriteria_treatments
                            ]
    

In [43]:
did_list = []
problems_list = []
tests_list = []
treatments_list = []

for i in tqdm(range(len(docs))):
#for i in range(1):
    
    with open(path + docs[i], "r") as f:
        text = f.read()
    
    tokenized_sentences, all_spans, normalized_text = parse_text(text)
    all_annotations = clinical_concept_extraction(tokenized_sentences)
    ent = build_display_elements(tokenized_sentences, all_annotations, all_spans)
    
    problems = []
    tests = []
    treatments = []

    for e in ent:
        text = normalized_text[e['start']:e['end']]
        if e['label'] == 'problem':
            problems.append(text)
        elif e['label'] == 'test':
            tests.append(text)
        elif e['label'] == 'treatment':
            treatments.append(text)
    
    did_list.append(docs[i][:-4])
    problems_list.append('_'.join(problems))
    tests_list.append('_'.join(tests))
    treatments_list.append('_'.join(treatments))

  0%|          | 0/100 [00:00<?, ?it/s]

INFO:tensorflow:Restoring parameters from /home2/dalya/clinical_concept_extraction/clinical_concept_extraction/cce_assets/blstm/model


  1%|          | 1/100 [00:25<42:37, 25.83s/it]

INFO:tensorflow:Restoring parameters from /home2/dalya/clinical_concept_extraction/clinical_concept_extraction/cce_assets/blstm/model


  2%|▏         | 2/100 [01:06<56:10, 34.39s/it]

...

 98%|█████████▊| 98/100 [1:09:43<01:44, 52.34s/it]

INFO:tensorflow:Restoring parameters from /home2/dalya/clinical_concept_extraction/clinical_concept_extraction/cce_assets/blstm/model


 99%|█████████▉| 99/100 [1:10:28<00:50, 50.21s/it]

INFO:tensorflow:Restoring parameters from /home2/dalya/clinical_concept_extraction/clinical_concept_extraction/cce_assets/blstm/model


100%|██████████| 100/100 [1:10:59<00:00, 42.60s/it]


In [1]:
all_annotations

NameError: name 'all_annotations' is not defined

In [45]:
ori_texts = []

for i in tqdm(range(len(docs))):
    
    with open(path + docs[i], "r") as f:
        text = f.read()
        ori_texts.append(text)

100%|██████████| 100/100 [00:00<00:00, 17456.63it/s]


In [48]:
os.getcwd()

'/home2/dalya/clinical_concept_extraction/ukyoung'

In [63]:
total_length = 100

df_output = pd.DataFrame({'Did': did_list,
                          'Problem': problems_list,
                          'ProblemCount': [ len(problems_list[i].split('_')) for i in range(total_length) ],
                          'Test': tests_list,
                          'TestCount': [ len(tests_list[i].split('_')) for i in range(total_length) ],
                          'Treatment': treatments_list,
                          'TreatmentCount': [ len(treatments_list[i].split('_')) for i in range(total_length) ],
                          'Doc': ori_texts})

df_output.to_csv('docs/clinical_100docs_with_origins.csv', header=True, index=False)
df_output.to_excel('docs/clinical_100docs_with_origins.xlsx', header=True, index=False)

In [7]:
cbert_term_list = []

cbert_term_list = problems_list
#for i in range(len(topics)):
#    cbert_term_list.append(problems_list[i] + tests_list[i] + treatments_list[i])
#    problems_list

In [8]:
## GET Topics -> ClinicalBert -> Termlist
print(topics[0])
print(cbert_term_list[0])


A 19-year-old male came to clinic with some sexual concern.  He recently engaged in a relationship and is worried about the satisfaction of his girlfriend. He has a "baby face" according to his girlfriend's statement and he is not as muscular as his classmates.  On physical examination, there is some pubic hair and poorly developed secondary sexual characteristics. He is unable to detect coffee smell during the examination, but the visual acuity is normal. Ultrasound reveals the testes volume of 1-2 ml. The hormonal evaluation showed serum testosterone level of 65 ng/dL with low levels of GnRH.

['some pubic hair', 'poorly developed secondary sexual characteristics', 'coffee smell', 'low levels of GnRH']


In [10]:
def get_phrases(topic):
    phrases = re.findall("\$\([A-z\s\d\-]+\)", topic)

    p_list = []
    for p in phrases:
        p_list.append(p[2:-1])

    return p_list

biobert_term_list = []

for i in range(len(df)):
    biobert_term_list.append(get_phrases(df['topics'][i]))

In [11]:
df_output = pd.DataFrame({'Topic': range(1, 51),
                          'Bio': biobert_term_list})

df_output.to_csv('BioBert_terms_2022.csv', header=True, index=False)

In [31]:
print(topics[43])
print(cbert_term_list[43])
print(biobert_term_list[43])


A 48-year-old man comes to the office complaining of heartburn and acid reflux.  He has taken over-the-counter antacids but sees no relief.  Other medical history is unremarkable.  The patient does not use tobacco, alcohol, or illicit drugs.  Vital signs are within normal limits.  BMI is 31 kg/m2.  Physical examination is  positive for mild tenderness in upper stomach. Chest x-ray shows an air-fluid opacity behind the heart.  A barium swallow study reveals approximately 1/3 of the stomach herniating through the esophageal hiatus. 

['heartburn', 'acid reflux', 'mild tenderness in upper stomach', 'an air-fluid opacity behind the heart', 'the stomach']
['heartburn', 'antacids', 'tobacco', 'illicit drugs', 'BMI', 'stomach', 'x-ray', 'barium', 'stomach']


In [21]:
from elasticsearch import Elasticsearch

urls = ["http://210.117.182.30:9200"]
es_host = Elasticsearch(urls, request_timeout=60)

# The list of fields to search
es_fields_for_cui = ["cui"]

# The name of index
es_index_for_cui = "idx-cui-terms"

In [22]:
def get_expanded_by_cui(text):
    
    body = {
        "_source": ["terms"], 
        "query": {
            "match": {
                "terms": text
            }
        }
    }
    
    res_cui = es_host.search(index=es_index_for_cui, body=body)
    res_cui = res_cui.get("hits").get("hits")
    if res_cui == []:
        return " "
        
    res_cui = res_cui[0]
    qe_text = res_cui.get('_source').get('terms')
    
    return qe_text

In [23]:
get_expanded_by_cui("urinary retention")
#get_expanded_by_cui("MRI")

/home/dalya/anaconda3/envs/dalya/lib/python3.6/site-packages/elasticsearch/connection/base.py:190: ElasticsearchDeprecationWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.17/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchDeprecationWarning)


' urinary retention retention, urinary retention urinary bladder distention bladder retention of urine bladder urine retention retention of urine retention urine nos urine retention retention urine retention; urine urine; retention bladder retention retention;bladder bladder; retention bladder inability to empty inability to empty bladder unable to empty bladder unable to pass urine retention of urine, unspecified retention of urine unspecified cannot pass urine - retention not passing urine bladder retention of urine -retired- cannot pass urine - retention (& ) retention of urine unspecified (context-dependent category) retention of urine (context-dependent category) retention - symptom rndx urinary retention'